In [1]:
import pandas as pd
import numpy as np
from sklearn.ensemble import RandomForestClassifier
from sklearn.preprocessing import StandardScaler, OneHotEncoder
from sklearn.compose import ColumnTransformer
from sklearn.pipeline import Pipeline
from sklearn.model_selection import train_test_split
from sklearn.metrics import classification_report
import plotly.express as px
from sklearn.model_selection import KFold, cross_val_score



In [2]:
data = pd.read_csv("Colorectal_Cancer_copy.csv")

In [13]:
data.shape

(167497, 28)

In [3]:
import pandas as pd
Colorectal_Cancer = pd.read_csv('Colorectal_Cancer_copy.csv', sep = ',')
Colorectal_Cancer

Patient_ID Country  Age Gender Cancer_Stage  Tumor_Size_mm  \
0                1      UK   77      M    Localized             69   
1                2      UK   59      M    Localized             33   
2                3   Japan   66      M     Regional             17   
3                4     USA   83      M     Regional             14   
4                5  France   66      M    Localized             34   
...            ...     ...  ...    ...          ...            ...   
167492      167493     USA   69      M    Localized             49   
167493      167494     USA   79      F     Regional             29   
167494      167495     USA   74      M   Metastatic             62   
167495      167496      UK   68      F    Localized             35   
167496      167497  France   79      F   Metastatic             67   

       Family_History Smoking_History Alcohol_Consumption Obesity_BMI  ...  \
0                  No              No                 Yes  Overweight  ...   
1                  No              No                  No  Overweight  ...   
2                  No             Yes                  No      Normal  ...   
3                  No              No                  No       Obese  ...   
4                  No             Yes                  No      Normal  ...   
...               ...             ...                 ...         ...  ...   
167492             No             Yes                  No  Overweight  ...   
167493            Yes             Yes                 Yes  Overweight  ...   
167494            Yes             Yes                 Yes      Normal  ...   
167495             No             Yes                 Yes      Normal  ...   
167496            Yes              No                  No       Obese  ...   

       Survival_5_years Mortality Healthcare_Costs Incidence_Rate_per_100K  \
0                   Yes        No            54413                      50   
1                   Yes        No            76553                      37   
2                   Yes        No            62805                      54   
3                   Yes        No            89393                      45   
4                   Yes        No            66425                      15   
...                 ...       ...              ...                     ...   
167492               No       Yes           100924                      57   
167493              Yes       Yes            90331                      39   
167494              Yes       Yes            90631                      13   
167495              Yes        No           114385                      18   
167496              Yes       Yes            47204                      14   

       Mortality_Rate_per_100K Urban_or_Rural Economic_Classification  \
0                            5          Urban               Developed   
1                           25          Urban              Developing   
2                           27          Urban               Developed   
3                           11          Urban               Developed   
4                           27          Urban              Developing   
...                        ...            ...                     ...   
167492                      13          Rural               Developed   
167493                      22          Urban               Developed   
167494                      19          Urban              Developing   
167495                      23          Urban               Developed   
167496                      17          Rural               Developed   

       Healthcare_Access Insurance_Status Survival_Prediction  
0               Moderate          Insured                 Yes  
1                   High        Uninsured                 Yes  
2               Moderate        Uninsured                  No  
3               Moderate          Insured                 Yes  
4                   High          Insured                 Yes  
...                  ...        

In [4]:
x= data['Survival_Prediction']
px.histogram(x)

In [5]:
x= data['Obesity_BMI']
px.histogram(x)

In [6]:
x= data['Smoking_History']
px.histogram(x)

In [7]:
feature_columns = ['Age','Tumor_Size_mm','Gender','Obesity_BMI','Smoking_History']
target_column = 'Survival_Prediction'

Model_Dataframe = data[feature_columns + [target_column]].copy()
Model_Dataframe.dropna(inplace=True)

In [8]:
X = Model_Dataframe[feature_columns]
y = Model_Dataframe[target_column]

numerical_features = ['Age', 'Tumor_Size_mm']
categorical_features = ['Gender', 'Obesity_BMI', 'Smoking_History']

preprocessor = ColumnTransformer(
    transformers=[ ('num', StandardScaler(), numerical_features),
                   ('cat', OneHotEncoder(drop='first', handle_unknown='ignore'), categorical_features)]
)

In [9]:
X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.2, random_state=32)

In [10]:
rf = Pipeline(steps=[ ('preprocessor', preprocessor),('classifier', RandomForestClassifier(random_state=30,class_weight='balanced'))])

rf.fit(X_train, y_train)

Pipeline(steps=[('preprocessor',
                 ColumnTransformer(transformers=[('num', StandardScaler(),
                                                  ['Age', 'Tumor_Size_mm']),
                                                 ('cat',
                                                  OneHotEncoder(drop='first',
                                                                handle_unknown='ignore'),
                                                  ['Gender', 'Obesity_BMI',
                                                   'Smoking_History'])])),
                ('classifier',
                 RandomForestClassifier(class_weight='balanced',
                                        random_state=30))])

In [11]:
rf = Pipeline(steps=[ ('preprocessor', preprocessor),('classifier', RandomForestClassifier(random_state=30,class_weight='balanced'))])

rf.fit(X_train, y_train)

Pipeline(steps=[('preprocessor',
                 ColumnTransformer(transformers=[('num', StandardScaler(),
                                                  ['Age', 'Tumor_Size_mm']),
                                                 ('cat',
                                                  OneHotEncoder(drop='first',
                                                                handle_unknown='ignore'),
                                                  ['Gender', 'Obesity_BMI',
                                                   'Smoking_History'])])),
                ('classifier',
                 RandomForestClassifier(class_weight='balanced',
                                        random_state=30))])

In [12]:
predictions = rf.predict(X_test)
kf = KFold(n_splits=5, shuffle=True, random_state=32)
score = cross_val_score(rf, X, y, cv=kf)

print(classification_report(y_test, predictions))
print("\n\n")
print(score)

print(f"Mean Score is ",{np.mean(score)})

              precision    recall  f1-score   support

          No       0.40      0.44      0.42     13468
         Yes       0.60      0.56      0.58     20032

    accuracy                           0.51     33500
   macro avg       0.50      0.50      0.50     33500
weighted avg       0.52      0.51      0.52     33500




[0.51310448 0.5118806  0.51419445 0.51514971 0.51434371]
Mean Score is  {np.float64(0.5137345891813211)}
